# Strava Activities Heatmapper

- [gpxpy](https://pypi.org/project/gpxpy/) - parsing GPX files
- [folium](https://pypi.org/project/folium/) - overlaying GPS data on maps

In [14]:
import os

import gpxpy
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import gzip
import folium

from tqdm import tqdm
from pathlib import Path

## Getting the data
1. Open [this link](https://www.strava.com/athlete/delete_your_account) and request your archive.
2. Once you get it on your e-mail, download it.
3. Unarchive the `activities` folder to the directory, containing this notebook and rename it to `activities_archived`.

In [3]:
Path('activities').mkdir(exist_ok=True)

Unarchiving the gpx files

In [23]:
for gpx_gz in os.listdir('activities_archived'):
    with gzip.open('activities_archived/{}'.format(gpx_gz)) as f_in:
        decompressed_name = ".".join(gpx_gz.split('.')[:-1])

        with open('activities/{}'.format(decompressed_name), 'wb') as f_out:
            f_out.write(f_in.read())

Utility function for getting activity points

In [9]:
def read_gpx_points(gpx_filename: str) -> pd.DataFrame:
    """
    Retrieves the coordinates of the track from the file under gpx_filename
    
    Parameters
    ----------
    gpx_filename(str) : filename of GPX to get coordinates from
    
    Returns
    -------
    (pd.DataFrame) : a dataframe, containing latitudes and longitudes of activity points
    
    Raises
    ------
    GPXException : when GPX is malformed or does not contain any coordinates (i.e. swimming session)
    """
    with open(gpx_filename) as f:
        gpx = gpxpy.parse(f)

        points = np.array(
            [[point[0].latitude, point[0].longitude]
                for point in gpx.tracks[0].segments[0].walk()]
        )

        return pd.DataFrame(points, columns=['lat', 'lng'])


Rendering the map with ovelaying routes

In [18]:
folium_map = folium.Map([coords_df['lat'].mean(), coords_df['lng'].mean()], zoom_start=11)

for gpx_filename in tqdm(os.listdir('activities')):
    try:
        coords_df = read_gpx_points(os.path.join('activities', gpx_filename))
        folium.PolyLine(coords_df.to_numpy(), color='blue', opacity=0.2).add_to(folium_map)
    except gpxpy.gpx.GPXException:
        # skip malformed activities
        pass

folium_map

100%|█████████████████████████████████████████| 119/119 [00:07<00:00, 16.98it/s]
